In [2]:
import pandas as pd
import numpy as np
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
import re

In [39]:
data = pd.read_csv("./review_pizza.csv",index_col=0)
#delete "date"
data.pop('date')
#sort by business, then reindex.
data=data.sort_values(by='business_id')
data.set_index('business_id')

stars                                               text
business_id                                                          
18             1.0  this place does not exist and the number left ...
18             5.0  I haven't been here in years, but they had the...
18             5.0  No reviews? Does this place even still exist? ...
24             1.0  So disappointed. The server gets 4 stars for b...
24             3.0  Service was pretty good, prices a little high,...
24             1.0  Wow, what a shame, the Greeks are gone and so ...
24             1.0  DRINKS: The selection is lacking. I wanted a g...
24             2.0  Usually go for the half price wings deal but t...
24             2.0  Ever since the place was sold this summer, the...
24             4.0  Probably the best wings in the city and cheap ...
24             1.0  We were the only table in the restaurant, a ta...
24             5.0  Had lamb shank to-day, ST. Patrick's Day.  It'...
24             3.0  Food was very good. Souvlaki and, I bet, homem...
24             1.0  Since the owner changed, this restaurant was j...
24             5.0  I loved this place. M friends and I went there...
24             1.0  Let me first off state, the star is strictly b...
24             2.0  Mt girlfriends family has made a tradition of ...
24             1.0  DRINKS: The selection is lacking. I wanted a g...
24             1.0  New owners at The Triple. They are having chal...
24             3.0  Good bar food at the back at a good price. Lot...
25             4.0  I have always enjoyed stuffed crust pizza and ...
25             1.0  This is the worst Pizza Hut I've ever been to....
25             4.0  I don't give many reviews for Chain Restaurant...
25             5.0  It's a Pizza Hut. Service may be slow much of ...
25             2.0  This Pizza Hut is pretty hit or miss on servic...
25             1.0  Placed order and paid online, received order c...
112            4.0  Oh yes delicious Pizza!  Everyone likes Pizza....
112            4.0  Yeah this place is ballin. The pizza here is r...
112            4.0  Love the pizza here! \nThis little pizza place...
112            5.0  The best pizza pie with 30 miles! Consistent, ...
...            ...                                                ...
192588         5.0  I took my girlfriend to Buon Gusto before ice ...
192588         5.0  Today's dinner meal was markedly better than o...
192588         3.0  A friend of mine introduced me to this place a...
192588         5.0  5 stars all the way! Mom called our food "home...
192588         3.0  My friend and I decided to come here a few day...
192588         4.0  Excellent service. The service is probably wha...
192588         4.0  Same restaurant - different location. We were ...
192588         5.0  I had the chicken cacciatore today. I'm a fan....
192588         4.0  This little place is so great!  In a strip mal...
192588         3.0  I was so hopeful that this would be a great ad...
192588         2.0  Well we're do I start.   \n\nOrdered a large p...
192588         4.0  I love the candlelit charm of an Italian resta...
192588         1.0  I used to love this place and am truly devasta...
192588         5.0  My wife and I usually go out to eat on Sundays...
192588         5.0  Awesome!  Da Best,\n\nOutside decor -  how can...
192588         5.0  Tiny little old school Italian joint with amaz...
192588         4.0  One of the best well rounded Italian restauran...
192588         4.0  Very cute little place with great service & de...
192588         2.0  I've been going to this place for 10 years but...
192588         1.0  Went in to use my buy one get one 50% off.  No...
192588         5.0  This is the real deal Italian food.   I never ...
192588         4.0  I came for dinner and ordered the meat ravioli...
192588         5.0  Buon gusto is what every other Italian restaur...
192588         4.0  Very nice place!!! relaxed, casual atmosphere ...
192588         4.0  Jus

In [40]:
data.loc[10,'text']

'Go. Seriously. You will not be disappointed one bit!\n\nWe were craving breakfast food and decided to check this place out. We shared a skillet and a few breakfast sides, each of which were cooked to perfection and super tasty. The atmosphere here is cute, clean, and just what you want for enjoying your breakfast. \n\nWhat really made our day being here was our awesome server, Tina. She was so cool, upbeat, easy to talk with, and was the most accommodating server you could ever hope to have. We plan on returning for more good eats and to see Tina again. :)'

In [45]:
#to quickly get text, only extract texts into a list.
t=[]
for i in range(data.shape[0]):
    t.append(data['text'][i].lower())

In [5]:
def check_word (word,source):
    res=[]
    for i in range(data.shape[0]):
        res.append(word in source[i])
    return sum(res)

In [6]:
check_word("no.1",t)
#'no.1' only appears 4 times, won't take it into account.

4

In [7]:
s=0
for i in range(1,6):
    s += check_word("%d star" % (i),t)
print(s)
#we can see there are lots of words(16631) indicating ratings, so further transformation is needed.

16631


In [8]:
#no idea how to deal with num+times form.
check_word("20 times",t)

90

In [46]:
for doc in range(data.shape[0]):
    t[doc]=re.sub('5\sstar[s]*','exellent',t[doc])
    t[doc]=re.sub('five\sstar[s]*','exellent',t[doc])
    t[doc]=re.sub('4\sstar[s]*','good',t[doc])
    t[doc]=re.sub('four\sstar[s]*','good',t[doc])
    t[doc]=re.sub('3\sstar[s]*','average',t[doc])
    t[doc]=re.sub('three\sstar[s]*','average',t[doc])
    t[doc]=re.sub('[12]\sstar[s]*','bad',t[doc])
    t[doc]=re.sub('two\sstar[s]*','bad',t[doc])
    t[doc]=re.sub('one\sstar','bad',t[doc])
    t[doc]=re.sub('[:;]+["^-]*\)+','pleased',t[doc])
    t[doc]=re.sub('[:;]+["^-]*\(+','frustrated',t[doc])
    t[doc]=re.sub('n\'t','not',t[doc])
    t[doc]=re.sub('\'d','',t[doc])
    t[doc]=re.sub('\'m','',t[doc])
    t[doc]=re.sub('\'re','',t[doc])
    t[doc]=re.sub('\'ll','',t[doc])
    t[doc]=re.sub('\'s','',t[doc])
    t[doc]=re.sub('[^A-Za-z0-9\s]','',t[doc])
    t[doc]=re.sub(r'\d+ (?!min)','',t[doc])
    t[doc]=re.sub('\n','',t[doc])

In [47]:
#test if re.sub works
t[11]

'my husband and i used to order from here more than i like to admit almost weekly the pizza is pretty mediocre but it really cheap and convenient the cheesy bread subs chicken fingers and onion rings are pretty delicious we always order online which i love it right around the corner delivery is always under 45 minutes yes we that lazy and really hate winter and the delivery people are always super nice sadly they had to go and screw up the good thing we had going last time we ordered it was for pickup as years of junk food ordering has taught me pickup to takes half the time of delivery we ordered cheesy bread a philly sub and onion rings i asked for ranch instead of marinara with the cheesy bread and requested ranch for the onion ringsi paid in advance and added a tip on takeout thinking that would help make up for any inconvenience or cost of my ranch requests we ordered the exact same thing for delivery the previous time with absolutely no problem by the way my husband showed up abo

In [48]:
data['text']=t

In [22]:
def word_split (doc):
    doc=re.split('\s*',doc)
    return doc

In [49]:
word_matrix=[]
for i in range(len(t)):
    word_matrix.append(word_split(t[i]))
#actualy it's a list of lists

/anaconda3/lib/python3.6/re.py:212: FutureWarning: split() requires a non-empty pattern match.
  return _compile(pattern, flags).split(string, maxsplit)


In [24]:
word_matrix
#words = set(nltk.corpus.words.words())
#for i in :
#   for j in :
#     if word_matrix[i][j] not in words:
#        print("non-en:%d,%d" % (i,j))
#length = len(sorted(word_matrix,key=len, reverse=True)[0])
#m=np.array([xi+[None]*(length-len(xi)) for xi in word_matrix])
#m

[['i',
  'be',
  'the',
  'first',
  'to',
  'admit',
  'that',
  'i',
  'was',
  'not',
  'excited',
  'about',
  'going',
  'to',
  'la',
  'tavolta',
  'being',
  'a',
  'food',
  'snob',
  'when',
  'a',
  'group',
  'of',
  'friends',
  'suggested',
  'we',
  'go',
  'for',
  'dinner',
  'i',
  'looked',
  'online',
  'at',
  'the',
  'menu',
  'and',
  'to',
  'me',
  'there',
  'was',
  'nothing',
  'special',
  'and',
  'it',
  'seemed',
  'overpriced',
  'im',
  'also',
  'not',
  'big',
  'on',
  'ordering',
  'pasta',
  'when',
  'i',
  'go',
  'out',
  'alas',
  'i',
  'was',
  'outnumbered',
  'thank',
  'goodness',
  'i',
  'ordered',
  'the',
  'sea',
  'bass',
  'special',
  'it',
  'was',
  'to',
  'die',
  'for',
  'cooked',
  'perfectly',
  'seasoned',
  'perfectly',
  'perfect',
  'portion',
  'i',
  'can',
  'not',
  'say',
  'enough',
  'good',
  'things',
  'about',
  'this',
  'dish',
  'when',
  'the',
  'server',
  'asked',
  'how',
  'it',
  'was',
  'he',
  

In [50]:
#l=[]
#for i in range(len(word_matrix)):
#    l.append(len(word_matrix[i]))
wordnet_lemmatizer = WordNetLemmatizer()
for i in range(len(word_matrix)):
    for j in range(len(word_matrix[i])):
        word_matrix[i][j]=wordnet_lemmatizer.lemmatize(word_matrix[i][j])

In [51]:
stop_words = set(stopwords.words('english'))
m=[]
for i in range(len(word_matrix)):
    m.append([w for w in word_matrix[i] if not w in stop_words])

In [29]:
#notice there're some errors in WordNetLemmatizer:
nltk.stem.WordNetLemmatizer().lemmatize('was')

'wa'

In [52]:
m

[['first',
  'admit',
  'wa',
  'excited',
  'going',
  'la',
  'tavolta',
  'food',
  'snob',
  'group',
  'friend',
  'suggested',
  'go',
  'dinner',
  'looked',
  'online',
  'menu',
  'wa',
  'nothing',
  'special',
  'seemed',
  'overpriced',
  'im',
  'also',
  'big',
  'ordering',
  'pasta',
  'go',
  'ala',
  'wa',
  'outnumbered',
  'thank',
  'goodness',
  'ordered',
  'sea',
  'bass',
  'special',
  'wa',
  'die',
  'cooked',
  'perfectly',
  'seasoned',
  'perfectly',
  'perfect',
  'portion',
  'say',
  'enough',
  'good',
  'thing',
  'dish',
  'server',
  'asked',
  'wa',
  'seemed',
  'proud',
  'dish',
  'said',
  'doesnot',
  'chef',
  'incredible',
  'job',
  'doe',
  'hubby',
  'got',
  'crab',
  'tortellini',
  'also',
  'loved',
  'heard',
  'mmmm',
  'good',
  'around',
  'table',
  'waiter',
  'wa',
  'super',
  'nice',
  'even',
  'gave',
  'u',
  'free',
  'dessert',
  'last',
  'people',
  'restaurant',
  'service',
  'wa',
  'slow',
  'place',
  'wa',
  'pa

In [60]:
cleaned_words=[]
for i in range(len(m)):
    cleaned_words.append([word for word in m[i] if len(word)>=3])

In [61]:
cleaned_words

[['first',
  'admit',
  'excited',
  'going',
  'tavolta',
  'food',
  'snob',
  'group',
  'friend',
  'suggested',
  'dinner',
  'looked',
  'online',
  'menu',
  'nothing',
  'special',
  'seemed',
  'overpriced',
  'also',
  'big',
  'ordering',
  'pasta',
  'ala',
  'outnumbered',
  'thank',
  'goodness',
  'ordered',
  'sea',
  'bass',
  'special',
  'die',
  'cooked',
  'perfectly',
  'seasoned',
  'perfectly',
  'perfect',
  'portion',
  'say',
  'enough',
  'good',
  'thing',
  'dish',
  'server',
  'asked',
  'seemed',
  'proud',
  'dish',
  'said',
  'doesnot',
  'chef',
  'incredible',
  'job',
  'doe',
  'hubby',
  'got',
  'crab',
  'tortellini',
  'also',
  'loved',
  'heard',
  'mmmm',
  'good',
  'around',
  'table',
  'waiter',
  'super',
  'nice',
  'even',
  'gave',
  'free',
  'dessert',
  'last',
  'people',
  'restaurant',
  'service',
  'slow',
  'place',
  'packed',
  'jug',
  'wine',
  'large',
  'group',
  'good',
  'conversation',
  'didnot',
  'seem',
  'bo

In [62]:
import csv
with open("corpus.csv", "w",newline="") as f:
    writer = csv.writer(f)
    writer.writerows(cleaned_words)